In [24]:
import folium
import matplotlib.cm as cm
import matplotlib.colors as cl


import openrouteservice as ors

# define colors
def color(value, maxValue):
    colors = ['#e31c00', '#aa5500', '#718e00', '#39c600', '#00ff00']
    N = len(colors)
    binSize = maxValue / N
    
    for i in range(N):
        if value < binSize*(i+1):
            return colors[i]
        

# create map centered on Heidelberg
m = folium.Map(location = [49.411085, 8.685894], zoom_start = 13)

# ORS expects [lon, lat]; Folium expects [lat, lon]
neuenheim = [[8.677139,49.412872],[8.690443,49.421080]]
neuenheim_folium = [list(reversed(coord)) for coord in neuenheim]

# query ORS locally
host = "http://localhost:8082/ors"
profile = "driving-car"
client = ors.Client(base_url=host)

resp = client.request(url = f'/v2/centrality/{profile}/json', get_params = {}, post_json = {'bbox': neuenheim})

# visualize rectangle
folium.Rectangle(bounds=neuenheim_folium, color='#fcba03', fill=True, fill_color='#fcba03').add_to(m) 
maxScore = max([node['score'] for node in resp['nodeScores']])
scores = {node['nodeId']: node['score'] for node in resp['nodeScores']}

# display centrality on map
for node in resp['locations']:
    nodeId = node['nodeId']
    folium.CircleMarker(location = list(reversed(node['coord'])),
                        radius = 1,
                        color=color(scores[nodeId], maxScore),
                        tooltip = f"id: {nodeId}, score: {scores[nodeId]}").add_to(m)
    
m

In [10]:
m2 = folium.Map(location = [49.411085, 8.685894], zoom_start = 13)

heidelberg = [[8.655705, 49.395446],[8.718184, 49.434366]]
heidelberg_folium = [[heidelberg[0][1], heidelberg[1][0]], [heidelberg[1][1],heidelberg[0][0]], [heidelberg[0][1], heidelberg[0][0]], [heidelberg[1][1],heidelberg[1][0]]]
  
resp = client.request(url = f'/v2/centrality/{profile}/json', get_params = {}, requests_kwargs = {"timeout":None}, post_json = {'bbox': heidelberg})
#resp = {'locations' : []};

# visualize rectangle
folium.Rectangle(bounds=heidelberg_folium, color='#fcba03', fill=True, fill_color='#fcba03').add_to(m2) 
maxValue = max(resp['centralityScores'])

# display centrality on map
count = 0
for loc in resp['locations']:
    loc[0], loc[1] = loc[1], loc[0]
    folium.CircleMarker(location = loc, tooltip = resp['nodeIds'][count], radius = 1, color=color(resp['centralityScores'][count], maxValue)).add_to(m2)
    count += 1
    
m2

In [12]:
m3 = folium.Map(location = [49.411085, 8.685894], zoom_start = 13)

heidelberg = [[8.655705, 49.395446],[8.718184, 49.434366]]
heidelberg_folium = [[heidelberg[0][1], heidelberg[1][0]], [heidelberg[1][1],heidelberg[0][0]], [heidelberg[0][1], heidelberg[0][0]], [heidelberg[1][1],heidelberg[1][0]]]

# exclude nodes corresponding to Theodor-Heuss-Brücke
resp_excluded = client.request(url = f'/v2/centrality/{profile}/json', get_params = {}, requests_kwargs = {"timeout":None}, post_json = {'bbox': heidelberg, 'excludeNodes':[6462,6463,11546,4967,7493]})

# visualize rectangle
folium.Rectangle(bounds=heidelberg_folium, color='#fcba03', fill=True, fill_color='#fcba03').add_to(m3) 
maxValue = max(resp_excluded['centralityScores'])

# display centrality on map
count = 0
for loc in resp_excluded['locations']:
    loc[0], loc[1] = loc[1], loc[0]
    folium.CircleMarker(location = loc, tooltip = resp_excluded['nodeIds'][count], radius = 1, color=color(resp_excluded['centralityScores'][count], maxValue)).add_to(m3)
    count += 1
    
m3

In [32]:
m4 = folium.Map(location = [49.411085, 8.685894], zoom_start = 13)

# color palette for diff visualization
def diffColor(value, maxDiffPercentage, minDiffPercentage):
    colors = ['#e31c00',  '#f39f93', '#ffffff', '#39c600', '#00ff00']
    if value < 0:
        if value < -(minDiffPercentage/2):
            return colors[0]
        else:
            return colors[1]
    elif value == 0:
        return colors[2]
    else:
        if value < maxDiffPercentage:
            return colors[3]
        else:
            return colors[4]      

# visualize rectangle
folium.Rectangle(bounds=heidelberg_folium, color='#fcba03', fill=True, fill_color='#fcba03').add_to(m4) 
maxValue = max(resp_excluded['centralityScores'])

new = {}
old = {}
ids = {}

count = 0
for loc in resp['locations']:
    locId = resp['nodeIds'][count]
    loc[0], loc[1] = loc[1], loc[0]
    ids[locId] = loc

    old[locId] = resp['centralityScores'][count]
    count += 1
    
count = 0
for loc in resp_excluded['locations']:
    locId = resp_excluded['nodeIds'][count]
    new[locId] = resp_excluded['centralityScores'][count]
    count += 1
    
maxDiffPercentage = 0
minDiffPercentage = 0
for locId in new:
    if old[locId] == 0:
        continue
    diffPercentage = ((new[locId] - old[locId])/old[locId])*100
    if diffPercentage > 0:
        if diffPercentage > maxDiffPercentage:
            maxDiffPercentage = diffPercentage
    elif diffPercentage < 0:
        if diffPercentage < minDiffPercentage:
            minDiffPercentage = diffPercentage
        
# display centrality on map
for locId in new:
    if old[locId] != 0:
        diffPercentage = ((new[locId] - old[locId])/old[locId])*100
    else:
        diffPercentage = 0
    folium.CircleMarker(location = ids[locId], tooltip = locId, radius = 1, color=diffColor(diffPercentage, maxDiffPercentage, minDiffPercentage)).add_to(m4)

m4